<a href="https://colab.research.google.com/github/r-petrella/ML_projects/blob/main/thesis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Libraries

In [1]:
pip install transformers

In [2]:
pip install hdbscan

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 34.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 81.4 MB/s eta 0:00:00
  Attempting uninstall: cython
    Found existing installation: Cython 3.0.10
    Uninstalling Cython-3.0.10:
      Successfully uninstalled Cython-3.0.10


In [3]:
pip install -U plotly==5.19.0

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.7/15.7 MB 25.8 MB/s eta 0:00:00
  Attempting uninstall: plotly
    Found existing installation: plotly 5.15.0
    Uninstalling plotly-5.15.0:
      Successfully uninstalled plotly-5.15.0


In [4]:
pip install pandas

In [5]:
pip install bertopic

  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl.metadata (1.8 kB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-manylinu

## Upload the corpus

In [6]:
from google.colab import files
uploaded = files.upload()

Saving scopus_20k.csv to scopus_20k.csv


In [7]:
import io
import pandas as pd
data = pd.read_csv(io.BytesIO(uploaded['scopus_20k.csv']))


## Retrieve two interesting columns from data

In [8]:
abstracts = data['Abstract']
titles = data['Title']

## Get the token from Hugging Face to call the LLM

In [9]:
from huggingface_hub import notebook_login
notebook_login()

## Perform 4-bit quantization to lighten the LLM

In [10]:
from torch import cuda

model_id = 'meta-llama/Llama-2-7b-chat-hf'
device = f'cuda:{cuda.current_device()}' if cuda.is_available() else 'cpu'

print(device)

cuda:0


In [11]:
pip install bitsandbytes

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 137.5/137.5 MB 16.5 MB/s eta 0:00:00


In [12]:
from torch import bfloat16
import transformers

# set quantization configuration to load large model with less GPU memory
# this requires the `bitsandbytes` library

bnb_config = transformers.BitsAndBytesConfig(
    load_in_4bit=True,  # 4-bit quantization
    bnb_4bit_quant_type='nf4',  # Normalized float 4
    bnb_4bit_use_double_quant=True,  # Second quantization after the first
    bnb_4bit_compute_dtype=bfloat16  # Computation type
)

## Set the LLM: llama 2 7b

In [13]:
# Llama 2 Tokenizer
tokenizer = transformers.AutoTokenizer.from_pretrained(model_id)

# Llama 2 Model
model = transformers.AutoModelForCausalLM.from_pretrained(
    model_id,
    trust_remote_code=True,
    quantization_config=bnb_config,
    device_map='auto',
)
#model = model.half().cuda()
model.eval()

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/1.62k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/414 [00:00<?, ?B/s]

...

model-00001-of-00002.safetensors:   0%|          | 0.00/9.98G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/3.50G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/188 [00:00<?, ?B/s]

LlamaForCausalLM(
  (model): LlamaModel(
    (embed_tokens): Embedding(32000, 4096)
    (layers): ModuleList(
      (0-31): 32 x LlamaDecoderLayer(
        (self_attn): LlamaSdpaAttention(
          (q_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (k_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (v_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (o_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (rotary_emb): LlamaRotaryEmbedding()
        )
        (mlp): LlamaMLP(
          (gate_proj): Linear4bit(in_features=4096, out_features=11008, bias=False)
          (up_proj): Linear4bit(in_features=4096, out_features=11008, bias=False)
          (down_proj): Linear4bit(in_features=11008, out_features=4096, bias=False)
          (act_fn): SiLU()
        )
        (input_layernorm): LlamaRMSNorm()
        (post_attention_layernorm): LlamaRMSNorm()
      )
    )
    (norm): Lla

## Parameter for text generation

In [14]:
# Our text generator
generator = transformers.pipeline(
    model=model, tokenizer=tokenizer,
    task='text-generation',
    temperature=0.4,
    max_new_tokens=8000,
    repetition_penalty=1.1
)

## Set the prompts to guide the LLM

In [15]:
# System prompt describes information given to all conversations
system_prompt = """
<s>[INST] <<SYS>>
You are a helpful, respectful and honest assistant for labeling topics.
<</SYS>>
"""

In [16]:
# Example prompt demonstrating the output we are looking for
example_prompt = """
I have a topic that contains the following documents:
- Psychological readiness following anterior cruciate ligament reconstruction (ACLR) correlates with different return to sport outcomes. However, the relationship between strength and power and psychological readiness remains unexplored. The aim of this study was to investigate the relationship between anterior cruciate ligament return to sport after injury (ACL-RSI) score...
- Background: Achilles tendon rupture is common among physically active individuals, yet a high percentage fail to return to their former activity after the injury. Quantifiable factors such as type of treatment, hours of rehabilitation, and age have not been associated with return-to-play rates. A factor that influences recovery is the participant’s experience before and throughout the rehabilitation process...
- The return to field is a critical moment for an athlete who has dislocated his shoulder as there is a significant risk of recurrence. The decision to return to field made by the doctor will therefore be crucial for the smooth continuation of the athlete's career. Hypothesis: This objective is to compare the criteria most used by specialists in clearing an overhead athlete to return to competition after a first episode of antero-internal dislocation of the glenohumeral joint with or without surgery...

The topic is described by the following keywords: 'return, to, the, criteria, athlete, and, by, of, quadriceps, achilles'.

Based on the information about the topic above, please create a very short label of this topic. Make sure you to only return the label and nothing more.

[/INST] Return to Sports Criteria After Injury
"""

In [17]:
# Our main prompt with documents ([DOCUMENTS]) and keywords ([KEYWORDS]) tags
main_prompt = """
[INST]
I have a topic that contains the following documents:
[DOCUMENTS]

The topic is described by the following keywords: '[KEYWORDS]'.

Based on the information about the topic above, please create a short label of this topic. Make sure you to only return the label and nothing more.
[/INST]
"""

In [18]:
prompt = system_prompt + example_prompt + main_prompt

## Embedding

In [19]:
from sentence_transformers import SentenceTransformer

# Pre-calculate embeddings
embedding_model = SentenceTransformer("BAAI/bge-small-en")
embeddings = embedding_model.encode(abstracts, show_progress_bar=True)
embeddings

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/90.8k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/52.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/684 [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/711k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

Batches:   0%|          | 0/625 [00:00<?, ?it/s]

array([[-0.04074085, -0.02305938,  0.00682972, ..., -0.05615811,
         0.05217776, -0.01082609],
       [-0.01773744, -0.00678086,  0.02960893, ..., -0.08243284,
         0.02831526,  0.00138619],
       [-0.03586454, -0.02530961,  0.02732268, ..., -0.05108161,
         0.05178559,  0.02192785],
       ...,
       [-0.06335061, -0.01502493,  0.01723955, ..., -0.03623749,
         0.01387563,  0.00147533],
       [-0.01094195, -0.03268239,  0.04085312, ..., -0.08055165,
         0.04507776,  0.03885034],
       [-0.01995889, -0.0178422 ,  0.01809282, ..., -0.04787526,
         0.02216915,  0.03348066]], dtype=float32)

In [20]:
type(embeddings)
print(embeddings.shape)

(20000, 384)


## Clustering

In [28]:
from umap import UMAP
from hdbscan import HDBSCAN

umap_model = UMAP(n_neighbors=15, n_components=5, min_dist=0.0, metric='cosine', random_state=42)
hdbscan_model = HDBSCAN(min_cluster_size=100, metric='euclidean', cluster_selection_method='eom', prediction_data=True)

In [29]:
# Pre-reduce embeddings for visualization purposes
reduced_embeddings = UMAP(n_neighbors=15, n_components=2, min_dist=0.0, metric='cosine', random_state=42).fit_transform(embeddings)

## Fine Tuning of Topics

In [30]:
from bertopic.representation import KeyBERTInspired, MaximalMarginalRelevance, TextGeneration

# KeyBERT
keybert = KeyBERTInspired()

# MMR
mmr = MaximalMarginalRelevance(diversity=0.3)

# Text generation with Llama 2
llama2 = TextGeneration(generator, prompt=prompt)

# All representation models
representation_model = {
    "KeyBERT": keybert,
    "Llama2": llama2,
    "MMR": mmr,
}

## Training

In [31]:
from bertopic import BERTopic

topic_model = BERTopic(

  # Sub-models
  embedding_model=embedding_model,
  umap_model=umap_model,
  hdbscan_model=hdbscan_model,
  representation_model=representation_model,

  # Hyperparameters
  top_n_words=10,
  verbose=True

)

# Train model
topics, probs = topic_model.fit_transform(abstracts, embeddings)

2024-07-31 19:27:02,677 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-07-31 19:27:28,230 - BERTopic - Dimensionality - Completed ✓
2024-07-31 19:27:28,232 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-07-31 19:27:29,432 - BERTopic - Cluster - Completed ✓
2024-07-31 19:27:29,439 - BERTopic - Representation - Extracting topics from clusters using representation models.
100%|██████████| 29/29 [08:26<00:00, 17.46s/it]
2024-07-31 19:36:05,141 - BERTopic - Representation - Completed ✓


## Results

In [35]:
# Show topics
info = topic_model.get_topic_info()
info

Topic  Count                                    Name  \
0      -1   5651                        -1_the_and_of_in   
1       0   3709                         0_and_the_of_in   
2       1   1579                    1_the_and_players_of   
3       2   1224                     2_acl_aclr_the_knee   
4       3   1132                       3_pain_the_and_of   
5       4    873              4_shoulder_the_of_patients   
6       5    807                  5_concussion_and_to_of   
7       6    632                    6_the_running_and_of   
8       7    558                7_cancer_and_exercise_of   
9       8    527                 8_covid_19_the_pandemic   
10      9    413                   9_hip_patients_and_of   
11     10    312           10_knee_osteoarthritis_oa_and   
12     11    229               11_achilles_tendon_the_of   
13     12    211              12_women_pregnancy_the_and   
14     13    204                   13_vr_the_and_virtual   
15     14    199            14_cai_ankle_instability_the   
16     15    173                    15_tendon_the_of_and   
17     16    153           16_bfr_flow_blood_restriction   
18     17    148                17_stretching_fr_rom_the   
19     18    148           18_prp_injection_platelet_the   
20     19    140        19_patellar_mpfl_dislocation_the   
21     20    138              20_eswt_the_treatment_pain   
22     21    137                21_ankle_the_ligament_of   
23     22    129               22_abstract_available_no_   
24     23    127         23_pfp_patellofemoral_pain_knee   
25     24    118                  24_activity_and_the_to   
26     25    112  25_cartilage_osteochondral_defects_the   
27     26    109   26_videos_quality_youtube_information   
28     27    108                27_ms_sclerosis_pwms_and   

                                       Representation  \
0    [the, and, of, in, to, with, were, for, was, on]   
1   [and, the, of, in, to, exercise, physical, wit...   
2   [the, and, players, of, in, to, athletes, trai...   
3   [acl, aclr, the, knee, reconstruction, of, and...   
4   [pain, the, and, of, to, in, with, back, lbp, ...   
5   [shoulder, the, of, patients, and, cuff, rotat...   
6   [concussion, and, to, of, injury, the, mtbi, i...   
7   [the, running, and, of, foot, to, in, for, gai...   
8   [cancer, and, exercise, of, the, to, in, breas...   
9   [covid, 19, the, pandemic, and, of, in, to, ph...   
10  [hip, patients, and, of, the, tha, to, were, t...   
11  [knee, osteoarthritis, oa, and, the, koa, of, ...   
12  [achilles, tendon, the, of, and, rupture, tend...   
13  [women, pregnancy, the, and, of, pregnant, pel...   
14  [vr, the, and, virtual, reality, to, of, exerg...   
15  [cai, ankle, instability, the, and, balance, w...   
16  [tendon, the, of, and, in, bone, cell, tissue,...   
17  [bfr, flow, blood, restriction, muscle, traini...   
18  [stretching, fr, rom, the, muscle, ss, and, of...   
19  [prp, injection, platelet, the, of, and, ha, k...   
20  [patellar, mpfl, dislocation, the, patients, p...   
21  [eswt, the, treatment, pain, in, extracorporea...   
22  [ankle, the, ligament, of, atfl, and, instabil...   
23            [abstract, available, no, , , , , , , ]   
24  [pfp, patellofemoral, pain, knee, pfps, and, w...   
25  [activity, and, the, to, of, step, for, walkin...   
26  [cartilage, osteochondral, defects, the, aci, ...   
27  [videos, quality, youtube, information, the, o...   
28  [ms, sclerosis, pwms, and, fatigue, multiple, ...   

                                              KeyBERT  \
0   [patients, injury, knee, intervention, exercis...   
1   [aerobic, exercise, interventions, sedentary, ...   
2   [sport, athletes, sports, injury, injuries, so...   
3   [acl, aclr, hamstring, ligament, injury, menis...   
4   [physiotherapy, physiotherapists, musculoskele...   
5   [arthroscopic, shoulder, tendon, glenohumeral,...   
6   [concussion, concussions, injury, injuries, tr...   
7   [treadmill, kinematics, gait, ru

In [36]:
info.iloc[:,6]  # keywords from MMR

0     [of, were, for, study, patients, results, musc...
1     [of, exercise, physical, health, pa, older, ad...
2     [players, athletes, training, were, injury, st...
3     [acl, aclr, knee, reconstruction, ligament, pa...
4     [pain, of, lbp, patients, chronic, disability,...
5     [shoulder, of, patients, rotator, pain, repair...
6     [concussion, injury, mtbi, symptom, tbi, athle...
7     [the, running, foot, gait, motion, runners, du...
8     [cancer, exercise, breast, survivors, patients...
9     [covid, pandemic, physical, during, health, in...
10    [hip, patients, tka, arthroscopy, arthroplasty...
11    [knee, osteoarthritis, oa, pain, exercise, pat...
12    [achilles, tendon, of, tendinopathy, patients,...
13    [women, pregnancy, pelvic, postpartum, menstru...
14    [vr, virtual, training, exergaming, physical, ...
15    [cai, ankle, instability, balance, sprain, lan...
16    [tendon, tissue, cells, healing, tendons, vitr...
17    [bfr, restriction, muscle, training, exercise,...
18    [stretching, muscle, massage, rolling, foam, f...
19    [prp, injection, platelet, knee, injections, o...
20    [patellar, mpfl, dislocation, patellofemoral, ...
21    [eswt, pain, extracorporeal, therapy, patients...
22    [ankle, ligament, atfl, lateral, tibiofibular,...
23    [abstract, available, no, , , , , , , , , , , ...
24    [patellofemoral, knee, pfps, hip, exercises, g...
25    [activity, walking, wearable, data, physical, ...
26    [cartilage, osteochondral, defects, aci, knee,...
27    [videos, youtube, jama, content, gqs, websites...
28    [ms, sclerosis, pwms, fatigue, exercise, edss,...
Name: MMR, dtype: object

Changing labels to llama2

In [37]:
llama2_labels = [label[0][0].split("\n")[0] for label in topic_model.get_topics(full=True)["Llama2"].values()]
topic_model.set_topic_labels(llama2_labels)


llama2_labels

['Return to Sports Criteria',
 'Exercise and Health in Older Adults',
 'Soccer Injury Prevention',
 'Return of Function After ACL Reconstruction',
 'Pain Management and Low Back Pain',
 'Shoulder Reconstruction Outcomes',
 'Concussion and Brain Injury',
 'Running and Foot Biomechanics',
 'Exercise Intervention for Breast Cancer Survivors',
 'Covid-19 Pandemic and Physical Activity',
 'Hip Preservation Surgery for Femoroacetabular Impingement Syndrome',
 'Knee Osteoarthritis Exercise Interventions',
 'Achilles Tendon Repair',
 "Pregnant Women's Knowledge and Perceptions of Exercise",
 'VR Exergaming for Rehabilitation',
 'Chronic Ankle Instability (CAI) and Balance',
 'Tendon Healing and Regeneration',
 'Blood Flow Restriction Training',
 'Stretching & Flexibility',
 'Platelet-Rich Plasma (PRP) Injections for Knee Osteoarthritis (OA)',
 'Patellar Instability Reconstruction',
 'Treatment of Pain in Extracorporeal Shockwave Therapy',
 'Ankle Ligament Repair',
 'Topic Label: No Abstract Av

In [38]:
topic_model.get_topic(4, full=True)["KeyBERT"]

[('arthroscopic', 0.85105526),
 ('shoulder', 0.8342184),
 ('tendon', 0.82336307),
 ('glenohumeral', 0.82167804),
 ('scapular', 0.8187983),
 ('biceps', 0.8153534),
 ('postoperative', 0.8139163),
 ('glenoid', 0.8129826),
 ('elbow', 0.8101274),
 ('preoperative', 0.80960166)]

In [41]:
topic_model.topic_representations_

{-1: [('the', 0.027116779649462276),
  ('and', 0.0252041014885738),
  ('of', 0.02381473752553463),
  ('in', 0.02116513810081357),
  ('to', 0.020024902931666436),
  ('with', 0.01598627514084096),
  ('were', 0.01535582785522513),
  ('for', 0.014772995295342236),
  ('was', 0.014741158753655677),
  ('on', 0.01118773640805483)],
 0: [('and', 0.025818731960385314),
  ('the', 0.024383599743415436),
  ('of', 0.022931491031151705),
  ('in', 0.02211630292928464),
  ('to', 0.020257682747238367),
  ('exercise', 0.017071567619601654),
  ('physical', 0.016996418825662735),
  ('with', 0.016642598749592178),
  ('for', 0.014470916032109591),
  ('were', 0.014242385301239535)],
 1: [('the', 0.02869907441906621),
  ('and', 0.026034140372052206),
  ('players', 0.024658128811646005),
  ('of', 0.02326816551579582),
  ('in', 0.02154356619170321),
  ('to', 0.020153925636669377),
  ('athletes', 0.018207509486782087),
  ('training', 0.01650862442219464),
  ('were', 0.014815752489936615),
  ('performance', 0.0143

## LDAvis

In [39]:
topic_model.visualize_topics(custom_labels=llama2_labels)

## UMAP with topics and Titles

In [43]:
topic_model.visualize_documents(titles, reduced_embeddings=reduced_embeddings,
                                custom_labels=llama2_labels, hide_annotations=True)

## Hierarchical clustering

In [44]:
from scipy.cluster import hierarchy as sch
from bertopic import BERTopic
topic_model = BERTopic()
topics, probs = topic_model.fit_transform(abstracts)

# Hierarchical topics
linkage_function = lambda x: sch.linkage(x, 'ward', optimal_ordering=True)
hierarchical_topics = topic_model.hierarchical_topics(titles, linkage_function=linkage_function)


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.7k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/612 [00:00<?, ?B/s]

...

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/joblib/externals/loky/backend/fork_exec.py:38: RuntimeWarning:

os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.

100%|██████████| 248/248 [00:01<00:00, 215.75it/s]


## Hierarchical clustering based on the c-TF-IDF matrix

In [45]:
hier_info = topic_model.get_topic_info()
hier_info

Topic  Count                                      Name  \
0       -1   6968                          -1_the_and_of_in   
1        0    822               0_concussion_mtbi_brain_tbi   
2        1    541        1_cancer_breast_survivors_exercise   
3        2    294  2_covid19_infection_postcovid19_sarscov2   
4        3    287              3_players_sprint_soccer_jump   
..     ...    ...                                       ...   
245    244     10                  244_bfr_aop_pvo_linearly   
246    245     10  245_addiction_problematic_chc_smartphone   
247    246     10      246_femoris_rectus_quadriceps_vastus   
248    247     10  247_prehabilitation_tka_prt_arthroplasty   
249    248     10              248_dsd_trunk_back_imbalance   

                                        Representation  \
0     [the, and, of, in, to, were, for, was, with, on]   
1    [concussion, mtbi, brain, tbi, symptom, sympto...   
2    [cancer, breast, survivors, exercise, chemothe...   
3    [covid19, infection, postcovid19, sarscov2, co...   
4    [players, sprint, soccer, jump, training, matc...   
..                                                 ...   
245  [bfr, aop, pvo, linearly, restriction, flow, s...   
246  [addiction, problematic, chc, smartphone, moun...   
247  [femoris, rectus, quadriceps, vastus, adjr2, r...   
248  [prehabilitation, tka, prt, arthroplasty, reha...   
249  [dsd, trunk, back, imbalance, sva, asymmetry, ...   

                                   Representative_Docs  
0    [Background: Total knee arthroplasty (TKA) is ...  
1    [Background: Concussion nondisclosure and poor...  
2    [Background: Many patients with metastatic bre...  
3    [BACKGROUND: Patients with severe coronavirus ...  
4    [This study aimed to assess the enhancement of...  
..                                                 ...  
245  [Applying blood flow restriction (BFR) during ...  
246  [Exercise addiction (EA) has been described as...  
247  [Introduction A shortened rectus femoris muscl...  
248  [BACKGROUND: The number of patients undergoing...  
249  [Background: Adequate trunk muscle endurance i...  

[250 rows x 5 columns]

In [46]:
topic_model.visualize_hierarchy(hierarchical_topics=hierarchical_topics, custom_labels=llama2_labels)


In [47]:
topic_model.get_topic(topic=7)

[('achilles', 0.03831262579415172),
 ('tendon', 0.030114277706387884),
 ('rupture', 0.01371182292481602),
 ('tendinopathy', 0.0124526150680075),
 ('atr', 0.00842654477872047),
 ('repair', 0.008300233216973986),
 ('ruptures', 0.007727749397429049),
 ('visaa', 0.007334674888567459),
 ('treatment', 0.006419594932535029),
 ('atrs', 0.006382119708234023)]

In [48]:
topic_model.get_document_info(abstracts)

Document  Topic  \
0      To identify biomarkers that precede the declin...     43   
1      Background: For athletes, overcoming obstacles...      5   
2      Aim: To identify the effects of strength and b...     14   
3      Major depressive disorder (MDD) is an increasi...     29   
4      Background: This study aimed to compare variou...      3   
...                                                  ...    ...   
19995  Selective medical perspectives of pediatric sp...      5   
19996  Physical activity has protective effects again...     -1   
19997  Accelerometers are low-cost measurement device...     23   
19998  Plantar fascia (PF) is a connective tissue mad...     36   
19999  BACKGROUND: There are conflicting reports on t...     55   

                                       Name  \
0             43_sarcopenia_muscle_mass_hgs   
1            5_athletes_sport_mental_sports   
2          14_cai_ankle_instability_balance   
3      29_depression_mental_health_physical   
4              3_players_sprint_soccer_jump   
...                                     ...   
19995        5_athletes_sport_mental_sports   
19996                      -1_the_and_of_in   
19997     23_gait_learning_accuracy_machine   
19998          36_plantar_fasciitis_foot_pf   
19999   55_stretching_flexibility_ss_static   

                                          Representation  \
0      [sarcopenia, muscle, mass, hgs, older, skeleta...   
1      [athletes, sport, mental, sports, anxiety, psy...   
2      [cai, ankle, instability, balance, inversion, ...   
3      [depression, mental, health, physical, activit...   
4      [players, sprint, soccer, jump, training, matc...   
...                                                  ...   
19995  [athletes, sport, mental, sports, anxiety, psy...   
19996   [the, and, of, in, to, were, for, was, with, on]   
19997  [gait, learning, accuracy, machine, neural, ne...   
19998  [plantar, fasciitis, foot, pf, heel, pain, fas...   
19999  [stretching, flexibility, ss, static, hamstrin...   

                                     Representative_Docs  \
0      [Objective: Sarcopenia is a common condition a...   
1      [Objectives: The aim of this study was to expl...   
2      [Background: Local pain around the ankle joint...   
3      [Background: Exercise referral schemes (ERS) r...   
4      [This study aimed to assess the enhancement of...   
...                                                  ...   
19995  [Objectives: The aim of this study was to expl...   
19996  [Background: Total knee arthroplasty (TKA) is ...   
19997  [Inertial measurement units (IMU) are widely u...   
19998  [Purpose.: Plantar fasciitis is the most frequ...   
19999  [Introduction: The effects of stretching exerc...   

                                             Top_n_words  Probability  \
0      sarcopenia - muscle - mass - hgs - older - ske...     0.114120   
1      athletes - sport - mental - sports - anxiety -...     0.767509   
2      cai - ankle - instability - balance - inversio...     1.000000   
3      depression - mental - health - physical - acti...     0.980754   
4      players - sprint - soccer - jump - training - ...     0.944619   
...                                                  ...          ...   
19995  athletes - sport - mental - sports - anxiety -...     0.799064   
19996  the - and - of - in - to - were - for - was - ...     0.000000   
19997  gait - learning - accuracy - machine - neural ...     1.000000   
19998  plantar - fasciitis - foot - pf - heel - pain ...     0.531256   
19999  stretching - flexibility - ss - static - hamst...     1.000000   

       Representative_document  
0                        False  
1                        False  
2                        False  
3                        False  
4                        False  
...                        ...  
19995                    False  
19996                    False  
19997                    False  
19998                    Fals

In [49]:
topic_model.get_representative_docs(topic=7)

['Purpose: Evaluate the one-year postoperative outcomes in patients with Chronic Achilles tendon rupture. Methods: Patients surgically treated for Chronic Achilles tendon rupture (n = 22, 14 males and 8 females, mean age 61 ± 15) were evaluated by Achilles tendon Total Rupture Score, The Physical Activity Scale, The Foot and Ankle Outcome Score, Calf muscle endurance test, counter movement jump, Hopping, ultrasound measurement of tendon length, Achilles Tendon Resting Angle, dorsi flexion range of motion and calf muscle circumference. Muscle function and tendon length outcomes on the injured side were compared with the healthy side. Results: The patients scored a mean of 62 ± 26 on the Achilles tendon Total Rupture Score. Median scores on the injured compared with the healthy side were lower in heel-rise repetitions (20 vs 24\xa0cm, p = 0.004), hel-rise height (8 vs 10\xa0cm, p < 0.001), heel-rise total work (872 vs 1590\xa0joule, p < 0.001) and hopping ratio (0.37 vs 0.48, p = 0.005).

In [50]:
reduced_model = topic_model.reduce_topics(abstracts, nr_topics=30)
reduced_model

In [46]:
# Show topics
info2 = reduced_model.get_topic_info()
info2

Topic  Count                                      Name  \
0      -1   6162                          -1_the_and_of_in   
1       0   3320                           0_the_and_of_to   
2       1   2281                           1_the_and_of_to   
3       2   1543                           2_and_the_of_to   
4       3   1410                           3_and_the_in_of   
5       4    979                    4_concussion_and_of_to   
6       5    956                     5_shoulder_the_of_and   
7       6    946                         6_pain_and_the_of   
8       7    383                      7_covid19_and_the_of   
9       8    345               8_children_physical_and_the   
10      9    225                       9_the_and_of_tendon   
11     10    204                          10_the_vr_and_to   
12     11    183                11_women_pregnancy_the_and   
13     12    169                 12_videos_the_of_articles   
14     13    135         13_cartilage_the_osteochondral_of   
15     14    129                 14_abstract_available_no_   
16     15     99                  15_sleep_quality_and_the   
17     16     92                       16_the_voice_of_and   
18     17     75        17_hamstring_groin_injury_injuries   
19     18     51      18_fixation_fractures_fracture_plate   
20     19     50             19_machine_learning_model_the   
21     20     44                20_ecg_cardiac_athletes_of   
22     21     41  21_causal_genetic_polymorphisms_genotype   
23     22     38          22_microbiota_gut_ibd_intestinal   
24     23     37                23_promis_reporting_of_the   
25     24     34          24_eswt_fasciotomy_treatment_the   
26     25     21  25_training_students_simulator_residents   
27     26     16                  26_exosomes_sci_cells_in   
28     27     16      27_sensing_sensor_sensors_monitoring   
29     28     16        28_hemophilia_haemophilia_pwh_sibs   

                                       Representation  \
0    [the, and, of, in, to, with, were, for, was, on]   
1   [the, and, of, to, with, knee, patients, in, w...   
2   [the, and, of, to, in, with, for, were, was, i...   
3   [and, the, of, to, cancer, in, physical, exerc...   
4   [and, the, in, of, exercise, to, muscle, with,...   
5   [concussion, and, of, to, the, in, brain, with...   
6   [shoulder, the, of, and, patients, to, in, wit...   
7   [pain, and, the, of, to, in, with, back, for, ...   
8   [covid19, and, the, of, in, patients, with, co...   
9   [children, physical, and, the, motor, of, in, ...   
10  [the, and, of, tendon, in, expression, oa, bon...   
11  [the, vr, and, to, of, for, telehealth, in, wi...   
12  [women, pregnancy, the, and, of, pelvic, pregn...   
13  [videos, the, of, articles, and, most, quality...   
14  [cartilage, the, osteochondral, of, patients, ...   
15            [abstract, available, no, , , , , , , ]   
16  [sleep, quality, and, the, of, in, to, psqi, o...   
17  [the, voice, of, and, oral, swallowing, in, to...   
18  [hamstring, groin, injury, injuries, adductor,...   
19  [fixation, fractures, fracture, plate, screw, ...   
20  [machine, learning, model, the, algorithms, of...   
21  [ecg, cardiac, athletes, of, the, in, and, hea...   
22  [causal, genetic, polymorphisms, genotype, act...   
23  [microbiota, gut, ibd, intestinal, and, the, o...   
24  [promis, reporting, of, the, and, to, for, qua...   
25  [eswt, fasciotomy, treatment, the, shock, of, ...   
26  [training, students, simulator, residents, ort...   
27  [exosomes, sci, cells, in, expression, cell, a...   
28  [sensing, sensor, sensors, monitoring, the, an...   
29  [hemophilia, haemophilia, pwh, sibs, with, in,...   

                                  Representative_Docs  
0   [Background: Exercise and dietary nutrition ar...  
1   [Introduction: Anterior cruciate ligament (ACL...  
2   [Background: Shoulder injuries are very common...  
3   [Background: Radiation therapy (RT) is given t...  
4   [Background: Electrical muscl

In [36]:
pip install nbconvert

In [40]:
!jupyter nbconvert --to html thesis.ipynb

[NbConvertApp] WARNING | pattern 'thesis.ipynb' matched no files
This application is used to convert notebook files (*.ipynb)
        to various other formats.


Options
The options below are convenience aliases to configurable class-options,
as listed in the "Equivalent to" description-line of the aliases.
To see all configurable class-options for some <cmd>, use:
    <cmd> --help-all

--debug
    set log level to logging.DEBUG (maximize logging output)
    Equivalent to: [--Application.log_level=10]
--show-config
    Show the application's configuration (human-readable format)
    Equivalent to: [--Application.show_config=True]
--show-config-json
    Show the application's configuration (json format)
    Equivalent to: [--Application.show_config_json=True]
--generate-config
    generate default config file
    Equivalent to: [--JupyterApp.generate_config=True]
-y
    Answer yes to any questions instead of prompting.
    Equivalent to: [--JupyterApp.answer_yes=True]
--execute
    Exec

@article{grootendorst2022bertopic,
  title={BERTopic: Neural topic modeling with a class-based TF-IDF procedure},
  author={Grootendorst, Maarten},
  journal={arXiv preprint arXiv:2203.05794},
  year={2022}
}
